In [2]:
import json
from ics import Calendar, Event
from ics.grammar.parse import ContentLine
import datetime
import os

In [36]:
with open('./data/therapists.json', 'r') as infile:
    loaded = json.load(infile)

print(f'{len(loaded)} entries loaded.')

with_mail = list(filter(lambda entry: 'mails' in entry, loaded))
print(f'{len(with_mail)} with email.')

with_vt = list(filter(lambda entry: 'Verhaltenstherapeutische Einzeltherapie – Erwachsene' in entry['therapy_types'], with_mail))
print(f'{len(with_vt)} with VT.')

allmails = []

for entry in with_vt:
    allmails += list(map(lambda mail: mail.lower(), entry['mails']))

allmails = list(set(allmails))

print(f'{len(allmails)} without duplicates.')

print(", ".join(allmails))

275 entries loaded.
169 with email.
89 with VT.
73 without duplicates.
info@psychotherapie-eitel.de, psychotherapie-spindler@web.de, praxis-v-kollenbaum@gmx.de, mail@praxis-sentuerk.de, info@praxis-kusche-mall.de, moers@psychotherapie-halbeis.de, praxis.stracke@tuta.com, praxis@schimanski-psychotherapie.de, praxisdoerner@gmx.de, buergerpraxiska@online.de, info@mrl-praxis.de, psychotherapie-koeck@posteo.de, psychotherapie.haeusser@gmx.com, praxis@psychotherapie-dölker.de, j.schmidt@praxis-p3.de, info@praxislott.de, hafferisabel@aol.com, praxis@psychotherapiewissen.de, praxis@psychotherapielutz.de, shrink1@web.de, praxis.klene-gaspard@t-online.de, kvt.diez@gmail.com, mail@gertrud-fahnenbruck.de, praxis.reventlow@gmx.de, noreen.weiler@protonmail.com, praxis@michael-schwehn.de, answer@stahl-eversberg.de, praxis@psychiatricum-ka.de, praxis.urban@outlook.com, praxis@brening-becker.de, praxis@drdamian.de, info@ptvo.de, praxis@wieske.de, hansbiewer@web.de, info@psychotherapiepraxis-borovac.de,

In [40]:
def mapday(day):
    return day.replace(' ', '').replace(':', '').lower()

In [41]:
def create_event(weekday, timeframe):
    appointment = Event()

    times = timeframe.split(' - ')
    begin = times[0].split(':')
    end = times[1].split(':')
    

    # All days have been validated to be one of ["Mo :", "Di :", "Mi :", "Do :", "Fr :"]
    # We just use the week this was developed at. Events recur weekly anyways…
    if weekday == 'Mo :':
        day = 7
    elif weekday == 'Di :':
        day =  8
    elif weekday == 'Mi :':
        day =  9
    elif weekday == 'Do :':
        day = 10
    elif weekday == 'Fr :':
        day = 11

    appointment.begin = datetime.datetime(2025, 4, day, int(begin[0]), int(begin[1]), 0)
    appointment.end = datetime.datetime(2025, 4, day, int(end[0]), int(end[1]), 0)

    appointment.extra.append(ContentLine(name="RRULE", value=f"FREQ=WEEKLY;INTERVAL=1;WKST=MO"))
    return appointment


In [54]:
def create_ics_files(therapists, path):
    # create a calendar for each therapist
    for therapist in therapists:
        # one .ics file per therapist
        therapist_calendar = Calendar()
        # extract all days
        for day in therapist['phone_appointments']:
            # create an event for each phone timeframe
            for i, phone_time in enumerate(therapist['phone_appointments'][day]):
                # non parsable times
                if len(phone_time.split(" - ")) != 2:
                    print(therapist['name'])

                appointment = create_event(day, phone_time)
                appointment.name = therapist['name']
                if 'phone' in therapist:
                    appointment.description = therapist['phone']
                therapist_calendar.events.add(appointment)

        # save appointment
        outpath = os.path.join(path, f'{therapist['name'].replace(' ', '_').replace('/', '&')}.ics')
        with open(outpath, "w+", newline='') as outfile:
            outfile.write(therapist_calendar.serialize())   

In [55]:
with open('./data/therapists.json', 'r') as infile:
    loaded = json.load(infile)

# only want the ones we can actually call
therapists = list(filter(lambda t: 'phone_appointments' in t and 'phone' in t, loaded))

print(f'{len(therapists)} of {len(loaded)} therapists callable.')

# filter for VT
with_vt = list(filter(lambda entry: 'Verhaltenstherapeutische Einzeltherapie – Erwachsene' in entry['therapy_types'], therapists))
print(f'{len(with_vt)} of {len(therapists)} therapists offer VT.')

create_ics_files(with_vt, os.path.join('data', 'icsfiles', 'with_vt'))


215 of 275 therapists callable.
113 of 215 therapists offer VT.
